In [1]:
%load_ext autoreload
%autoreload 2
# add . to module name
import sys
sys.path.append('../src/')

In [2]:
from package.logger import Timed, rlog, setup
from package import storage
setup("WARNING")

In [3]:
import os

import folium
import geopandas as gpd
import pandas as pd

from package import strtime
from package.osm import osm
from package.mcr.data import MCRGeoData
from package.mcr5.h3 import (
    get_h3_cells_for_nodes,
    get_h3_cells_for_bbox,
    plot_h3_cells_on_folium,
)
from package.mcr5.h3_osm_interaction import get_location_mappings_for_cells
from package.mcr5.mcr5 import MCR5
from package.osm.osm import add_nearest_osm_node_id
from package.mcr5.labels import read_labels_for_nodes
from package.minute_city import minute_city


In [4]:
city_id = "Koeln"
stops_path = "../data/cleaned/stops.csv"
osm_path = osm.get_osm_path_from_city_id(city_id)

with Timed.info("Reading stops"):
	other_stops_df = storage.read_gdf(stops_path)

if not os.path.exists(osm_path) and city_id:
	rlog.info("Downloading OSM data")
	osm.download_city(city_id, osm_path)
else:
	rlog.info("Using existing OSM data")

osm_reader = osm.new_osm_reader(osm_path)

with Timed.info("Getting OSM graph"):
	nodes, edges = osm.get_graph_for_city_cropped_to_stops(osm_reader, other_stops_df)

In [5]:
h3_cells = get_h3_cells_for_nodes(nodes[["lat", "lon"]].to_dict("records"), 9)
m = folium.Map(location=[50.9333, 6.95], zoom_start=12)
plot_h3_cells_on_folium(h3_cells, m)
m

In [6]:
h3_cells = get_h3_cells_for_nodes(nodes[["lat", "lon"]].to_dict("records"), 9)

In [7]:
location_mappings, invalid_h3_cells = get_location_mappings_for_cells(list(h3_cells), nodes, 20)
invalid_h3_cells

[]

In [8]:
m = folium.Map(location=[50.9375, 6.9603], zoom_start=12)
plot_h3_cells_on_folium(map(lambda lm: lm.h3_cell, location_mappings), m)
nodes_by_id = nodes.set_index("id")
for location_mapping in location_mappings:
	node = nodes_by_id.loc[location_mapping.osm_node_id]
	folium.CircleMarker(
		location=(node.lat, node.lon),
		icon=folium.Icon(color="green"),
		radius=1,
		color="red",
	).add_to(m)
m

In [9]:
stops = "../data/cleaned/stops.csv"
city_id = "Koeln"
structs = "../data/structs.pkl"


In [10]:
import geopandas as gpd
from package.osm import osm, graph

bicycle_location_path = "../data/bicycle_locations/2022-11-01_09_01_00.csv"
bicycle_locations = storage.read_df(bicycle_location_path)

stops_df = storage.read_gdf(stops_path)
osm_reader = osm.get_osm_reader_for_city_id_or_osm_path(city_id, None)
(
	osm_nodes,
	osm_edges,
) = osm.get_graph_for_city_cropped_to_stops(osm_reader, stops_df)
nxgraph = graph.create_nx_graph(osm_reader, osm_nodes, osm_edges)
nxgraph, osm_nodes, osm_edges = graph.crop_graph_to_largest_component(
	nxgraph, osm_nodes, osm_edges
)

bicycle_locations = gpd.GeoDataFrame(
	bicycle_locations,
	geometry=gpd.points_from_xy(
		bicycle_locations.lon,
		bicycle_locations.lat,
	),
)

osm.crop_to_nodes(bicycle_locations, osm_nodes)

lat       lon                  geometry
26    50.935349  6.900481  POINT (6.90048 50.93535)
27    50.943157  7.002093  POINT (7.00209 50.94316)
29    50.959709  6.996068  POINT (6.99607 50.95971)
31    50.967171  6.894573  POINT (6.89457 50.96717)
32    50.909214  6.993517  POINT (6.99352 50.90921)
...         ...       ...                       ...
1492  50.961361  7.004114  POINT (7.00411 50.96136)
1493  50.975285  7.007419  POINT (7.00742 50.97528)
1494  50.959141  7.008940  POINT (7.00894 50.95914)
1495  50.944199  7.001608  POINT (7.00161 50.94420)
1496  50.964500  6.953253  POINT (6.95325 50.96450)

[1165 rows x 3 columns]

In [11]:
mcr_geo_data = MCRGeoData(
    stops,
    structs,
    city_id,
    bicycle_location_path="../data/bicycle_locations/2022-11-01_09_01_00.csv",
)


In [12]:
# lat = 50.94640350341797
# lon = 7.019803047180176

# nearest_osm_node_id = 3605858836

# m = folium.Map(location=[lat, lon], zoom_start=12)

# folium.CircleMarker(
# 	location=(lat, lon),
# 	icon=folium.Icon(color="green"),
# 	radius=1,
# 	color="red",
# 	popup="Bicycle location",
# ).add_to(m)

# nearest_osm_node = osm_nodes[osm_nodes.id == nearest_osm_node_id].iloc[0]
# folium.CircleMarker(
# 	location=(nearest_osm_node.lat, nearest_osm_node.lon),
# 	icon=folium.Icon(color="green"),
# 	radius=1,
# 	color="red",
# 	popup="Nearest OSM node",
# ).add_to(m)
# m	

# for node in osm_nodes.sample(1000).itertuples():
# 	folium.CircleMarker(
# 		location=(node.lat, node.lon),
# 		icon=folium.Icon(color="green"),
# 		radius=1,
# 		color="black",
# 	).add_to(m)
# m

In [13]:
mcr5 = MCR5(geo_data=mcr_geo_data)

In [14]:
pois = minute_city.fetch_pois_for_area(nodes.unary_union.convex_hull, nodes)
mcr_geo_data.add_pois_to_mm_graph(pois)

In [15]:
location_mappings = location_mappings[:100]

In [16]:
mcr5_output_path = "../data/mcr5/Koeln"

In [17]:
errors = mcr5.run(location_mappings, start_time="08:00:00", output_dir=mcr5_output_path)

Starting:   0%|          | 0/100 [00:00<?, ?it/s]

1m 24.5s - without limits  
0m 34.4s - with limits

12m 54.0s - without limits  
5m 0.5s - with limits